<a href="https://colab.research.google.com/github/chldydgh4687/PRproject/blob/master/Bowspatialpyramidmatching.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [4]:
!ls -lha kaggle.json

!pip uninstall -y kaggle
!pip install --upgrade pip
!pip install kaggle==1.5.6


# 캐글연동을 위한 토큰 입력
! mkdir -p ~/.kaggle
! cp kaggle.json ~/.kaggle/
! chmod 600 ~/.kaggle/kaggle.json


# 버전이 1.5.6 이 아니면, 진행할 수 없다
! kaggle -v

-rw-r--r-- 1 root root 66 Dec  2 03:59 kaggle.json
Uninstalling kaggle-1.5.6:
  Successfully uninstalled kaggle-1.5.6
Requirement already up-to-date: pip in /usr/local/lib/python3.6/dist-packages (19.3.1)
Processing /root/.cache/pip/wheels/57/4e/e8/bb28d035162fb8f17f8ca5d42c3230e284c6aa565b42b72674/kaggle-1.5.6-cp36-none-any.whl
Kaggle API 1.5.6


In [2]:
! kaggle competitions download -c 2019-ml-finalproject

 97% 63.0M/65.0M [00:01<00:00, 23.2MB/s]
100% 65.0M/65.0M [00:01<00:00, 40.4MB/s]


In [0]:
import zipfile
import os

os.mkdir('/content/input')

zip_ref = zipfile.ZipFile("/content/2019-ml-finalproject.zip", 'r')
zip_ref.extractall("/content/input")
zip_ref.close()

In [5]:
! yes | pip3 uninstall opencv-python
! yes | pip3 uninstall opencv-contrib-python
! yes | pip3 install opencv-python==3.4.2.16
! yes | pip3 install opencv-contrib-python==3.4.2.16

Uninstalling opencv-python-3.4.2.16:
  Would remove:
    /usr/local/lib/python3.6/dist-packages/cv2/*
    /usr/local/lib/python3.6/dist-packages/opencv_python-3.4.2.16.dist-info/*
Proceed (y/n)?   Successfully uninstalled opencv-python-3.4.2.16
Uninstalling opencv-contrib-python-3.4.2.16:
  Would remove:
    /usr/local/lib/python3.6/dist-packages/opencv_contrib_python-3.4.2.16.dist-info/*
Proceed (y/n)?   Successfully uninstalled opencv-contrib-python-3.4.2.16
  Using cached https://files.pythonhosted.org/packages/fa/7d/5042b668a8ed41d2a80b8c172f5efcd572e3c046c75ae029407e19b7fc68/opencv_python-3.4.2.16-cp36-cp36m-manylinux1_x86_64.whl
ERROR: albumentations 0.1.12 has requirement imgaug<0.2.7,>=0.2.5, but you'll have imgaug 0.2.9 which is incompatible.
  Using cached https://files.pythonhosted.org/packages/08/f1/66330f4042c4fb3b2d77a159db8e8916d9cdecc29bc8c1f56bc7f8a9bec9/opencv_contrib_python-3.4.2.16-cp36-cp36m-manylinux1_x86_64.whl


In [0]:
import pandas as pd
import numpy as np
import cv2
import matplotlib.pyplot as plt
import os
import torch
from PIL import Image
from torch.utils.data import DataLoader, TensorDataset
from sklearn.preprocessing import StandardScaler
from tqdm import tqdm_notebook as tqdm

import glob

In [0]:
df_data = pd.read_csv('/content/input/Label2Names.csv', header=None)

In [7]:
cv2.__version__

'3.4.2'

In [0]:
def TrainDenseSIFT(path):
  data_des = list()
  data_images = list()
  data_label = list()
  data_set = list()

  Step_size = 6
  img_size = 256
 
  for cls in tqdm(os.listdir(path)):
    img_list = os.listdir(path+'/'+cls)
    img_list.sort()
    if cls == 'BACKGROUND_Google':
      label = 102
    else :
      label = (df_data.index[df_data[1]==cls] +1).tolist()[0]


    for img in img_list:

      image = cv2.imread(path + '/' + cls + '/' + img)
      gray = cv2.cvtColor(image,cv2.COLOR_BGR2GRAY)
      gray = cv2.resize(gray, (img_size, img_size))

      sift = cv2.xfeatures2d.SIFT_create()
#compute dense
      kp = [cv2.KeyPoint(x,y, Step_size) for y in range(0, gray.shape[0], Step_size) for x in range(0, gray.shape[1],Step_size)]
      keypoint, des = sift.compute(gray, kp)

      data_set.append(des)
      data_des.append(des)
      data_images.append(gray)
      data_label.append(label)

  return data_set, data_des, data_images, data_label

In [0]:
def TestDenseSIFT(path):

  img_size = 256
  Step_size = 4
  test_des = list()
  test_images = list()
  test_set = list()

  img_list = os.listdir(path)
  img_list.sort()

  for img in tqdm(img_list):
    image = cv2.imread(path + '/' + img)
    gray = cv2.cvtColor(image,cv2.COLOR_BGR2GRAY)
    gray = cv2.resize(gray, (img_size, img_size))
  
    sift = cv2.xfeatures2d.SIFT_create()

    kp = [cv2.KeyPoint(x,y, Step_size) for y in range(0, gray.shape[0], Step_size) for x in range(0, gray.shape[1],Step_size)]
    keypoint, des = sift.compute(gray, kp)

    test_set.append(des)
    test_des.append(des)
    test_images.append(gray)

  return test_set, test_des, test_images

In [11]:
train_data, train_des, train_image, train_label = TrainDenseSIFT("/content/input/train")

In [12]:
test_data, test_des, test_image = TestDenseSIFT("/content/input/testAll_v2")

In [13]:
train_des = np.array(train_des)
train_des.shape

(3060, 1849, 128)

In [14]:
test_des = np.array(test_des)
test_des.shape

(1692, 4096, 128)

In [15]:
train_des=train_des.reshape(-1,128)
train_des.shape

(5657940, 128)

In [16]:
test_des = test_des.reshape(-1,128)
test_des.shape

(6930432, 128)

In [17]:
pip install kmc2

In [0]:
import kmc2 
from sklearn.cluster import MiniBatchKMeans
import copy

In [0]:
seeding = kmc2.kmc2(train_des, 200)
kmeans = MiniBatchKMeans(200,init=seeding).fit(train_des)
codebook = kmeans.cluster_centers_

In [0]:
def formTrainingSetHistogram(train_data, kmeans, k):
  train_hist = []
  for i in range(len(train_data)):
    data = copy.deepcopy(train_data[i])
    predict = kmeans.predict(data)
    train_hist.append(np.bincount(predict, minlength = k).reshape(1,-1).ravel())
  return np.array(train_hist)

In [0]:
train_hist = formTrainingSetHistogram(train_data, kmeans, 200)
test_hist = formTrainingSetHistogram(test_data, kmeans, 200)

In [0]:
from sklearn.preprocessing import StandardScaler

In [0]:
train_scaler = StandardScaler().fit(train_hist)
train_hist = train_scaler.transform(train_hist)

test_hist = train_scaler.transform(test_hist)

In [0]:
from sklearn.svm import SVC
from sklearn.decomposition import PCA as RandomizedPCA

from sklearn.pipeline import make_pipeline

pca = RandomizedPCA(n_components=150, whiten=True, random_state=42)
svc = SVC(kernel='linear', class_weight='balanced')
model = make_pipeline(pca, svc)

In [0]:
from sklearn.model_selection import GridSearchCV


param_grid = {'svc__C': [1, 5, 10, 50],
              'svc__gamma': [0.0001, 0.0005, 0.001, 0.005]}
grid = GridSearchCV(model, param_grid)

%time grid.fit(train_hist, train_label)
print(grid.best_params_)

In [0]:
model = grid.best_estimator_
yfit = model.predict(test_hist)
yfit.shape

In [0]:
img_list = os.listdir("/content/input/testAll_v2")
img_list.sort()

In [0]:
yfit = yfit.reshape(-1,1)
result_img_list = np.array(img_list).reshape(-1,1)
total_result = np.hstack([result_img_list,yfit])

In [0]:
df = pd.DataFrame(total_result, columns=["Id","Category"])
df.to_csv('results-yongho-v3.csv',index=False, header=True)

In [0]:
! kaggle competitions submit -c 2019-ml-finalproject -f results-yongho-v3.csv -m "Final_Term_Project"

In [0]:
import math

def extract_denseSIFT(img):
  Step_size = 4
  sift = cv2.xfeatures2d.SIFT_create()
#compute dense
  kp = [cv2.KeyPoint(x,y, Step_size) for y in range(0, img.shape[0], Step_size) for x in range(0, img.shape[1],Step_size)]
  keypoint, des = sift.compute(img, kp)

  return des


# form histogram with Spatial Pyramid Matching upto level L with codebook kmeans and k codewords
def getImageFeaturesSPM(L, img, kmeans, k):
    W = img.shape[1]
    H = img.shape[0]   
    h = []
    for l in range(L+1):
        w_step = math.floor(W/(2**l))
        h_step = math.floor(H/(2**l))
        x, y = 0, 0
        for i in range(1,2**l + 1):
            x = 0
            for j in range(1, 2**l + 1):                
                desc = extract_denseSIFT(img[y:y+h_step, x:x+w_step])                
                #print("type:",desc is None, "x:",x,"y:",y, "desc_size:",desc is None)
                predict = kmeans.predict(desc)
                histo = np.bincount(predict, minlength=k).reshape(1,-1).ravel()
                weight = 2**(l-L)
                h.append(weight*histo)
                x = x + w_step
            y = y + h_step
            
    hist = np.array(h).ravel()
    # normalize hist
    dev = np.std(hist)
    hist -= np.mean(hist)
    hist /= dev
    return hist


# get histogram representation for training/testing data
def getHistogramSPM(L, data, kmeans, k):    
    x = []
    for i in range tqdm((len(data))):        
        hist = getImageFeaturesSPM(L, data[i], kmeans, k)        
        x.append(hist)
    return np.array(x)

In [20]:
seeding = kmc2.kmc2(train_des, 200)
kmeans = MiniBatchKMeans(200,init=seeding).fit(train_des)
codebook = kmeans.cluster_centers_

/usr/local/lib/python3.6/dist-packages/ipykernel_launcher.py:2: RuntimeWarning: Explicit initial center position passed: performing only one init in MiniBatchKMeans instead of n_init=3
  


In [21]:
train_image = np.array(train_image)
train_image.shape

(3060, 256, 256)

In [25]:
train_histo = getHistogramSPM(2, train_image, kmeans, 200)


In [26]:
test_histo = getHistogramSPM(2, test_image, kmeans, 200)

In [0]:
train_scaler = StandardScaler().fit(train_histo)
train_histo = train_scaler.transform(train_histo)

test_histo = train_scaler.transform(test_histo)

In [0]:
from sklearn.svm import SVC
from sklearn.decomposition import PCA as RandomizedPCA

from sklearn.pipeline import make_pipeline

pca = RandomizedPCA(n_components=150, whiten=True, random_state=42)
svc = SVC(kernel='linear', class_weight='balanced')
model = make_pipeline(pca, svc)

In [31]:
from sklearn.model_selection import GridSearchCV


param_grid = {'svc__C': [0.01, 0.05, 0.1, 0.5 , 1],
              'svc__gamma': [0.00001, 0.0001, 0.0005, 0.001, 0.005]}
grid = GridSearchCV(model, param_grid)

%time grid.fit(train_histo, train_label)
print(grid.best_params_)

/usr/local/lib/python3.6/dist-packages/sklearn/model_selection/_split.py:1978: FutureWarning: The default value of cv will change from 3 to 5 in version 0.22. Specify it explicitly to silence this warning.
  warnings.warn(CV_WARNING, FutureWarning)


CPU times: user 8min 40s, sys: 2min 35s, total: 11min 16s
Wall time: 5min 8s
{'svc__C': 0.05, 'svc__gamma': 1e-05}


In [32]:
model = grid.best_estimator_
yfit = model.predict(test_histo)
yfit.shape

(1692,)

In [0]:
img_list = os.listdir("/content/input/testAll_v2")
img_list.sort()

In [0]:
yfit = yfit.reshape(-1,1)
result_img_list = np.array(img_list).reshape(-1,1)
total_result = np.hstack([result_img_list,yfit])

In [0]:
df = pd.DataFrame(total_result, columns=["Id","Category"])
df.to_csv('results-yongho-v3.csv',index=False, header=True)

In [36]:
! kaggle competitions submit -c 2019-ml-finalproject -f results-yongho-v3.csv -m "Final_Term_Project"

100% 29.6k/29.6k [00:08<00:00, 3.44kB/s]
Successfully submitted to 2019.Fall.PatternRecognition 

## #0 (Developing)

### #0 Using Google Colab with GitHub ( Git Clone - branch : Develop )

In [0]:
!git config --global user.email "s2blue4687@naver.com"
!git config --global user.name "chldydgh4687"
!git clone -b Develop https://github.com/chldydgh4687/PRproject.git

### #0 code upload (Release - branch : Develop)

![대체 텍스트](https://github.com/chldydgh4687/PRproject/blob/Develop/study/picture/23423423.PNG?raw=true)

### #0 code upload (branch merge / push, pull - Gitkraken )

## #0 (Release) Using Google Colab with GitHub ( Git Clone - branch : Master )

In [0]:
!git config --global user.email "s2blue4687@naver.com"
!git config --global user.name "chldydgh4687"
!git clone -b master https://github.com/chldydgh4687/PRproject.git

# ##import Library